In [2]:
!pip install --upgrade pip

    100% |████████████████████████████████| 1.3MB 409kB/s eta 0:00:01
  Found existing installation: pip 9.0.3
    Uninstalling pip-9.0.3:
      Successfully uninstalled pip-9.0.3


In [1]:
!pip install pattern

    100% |████████████████████████████████| 24.6MB 15kB/s  eta 0:00:01
  Running setup.py bdist_wheel for pattern ... done
  Stored in directory: /home/nbuser/.cache/pip/wheels/0b/2d/69/9dad482e933f79b7ab35fa8e96c95e7e557655d27812c4f8d5
Successfully built pattern
You are using pip version 9.0.3, however version 10.0.1 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.


In [153]:
from pattern.en import parse, pprint, parsetree, wordnet

from pattern.vector import Document, Model, TFIDF
from pattern.vector import stem, PORTER, LEMMA
from pattern.vector import SVM, RADIAL, gridsearch, kfoldcv, count
from pattern.vector import distance, COSINE, tfidf

# For Latent Semantic Analysis (LSA)
from numpy.linalg import svd
from numpy import dot, diag

import re
from collections import Counter

In [3]:
sentence = "This is a test sentence that will be used to parse into a parse tree and various other things like spies."

In [159]:
qlines = list()
alines = list()
# corpus = list()
documents = list()
qaDocs = list()
container = list()

In [160]:
def readAndCreateCorpus():
    with open("FAQs.txt") as f:
        for line in f:
            if(re.match(r"^[0-9]{1,}.", line)):
                question = re.sub(r"^[0-9]{1,}. (.*)", "\\1", line)
                qlines.append(question)
                pass
            elif(re.match(r"^[A].", line)):
                answer = re.sub(r"^[A]. (.*)", "\\1", line)
                alines.append(answer)
                pass
            pass
        pass
    
    for i in range(len(qlines)):
        qa = qlines[i] + alines[i]
        # corpus.append(qa)
        # documents.append({"Q" : qlines[i], "A" : alines[i]})
        documents.append(qa)
        pass
    pass

In [161]:
readAndCreateCorpus()

In [164]:
def createContainer():
    for i in range(len(documents)):
        qaDocs.append(Document(documents[i], stemmer = LEMMA, name = "DOC {}".format(i)))
        
        # pos = parse(documents[i], lemmata = True)
        parse_tree = parsetree(documents[i], lemmata = True)
        
        word = None
        pos = None
        lemma = None
        stemmed = None
        wordnetted = dict()
        
        for sentence in parse_tree:
            for chunk in sentence.chunks:
                for w in chunk.words:
                    word = w.string
                    pos = w.pos
                    lemma = w.lemma
                    stemmed = stem(word)
                    
                    hypernyms = list()
                    hyponyms = list()
                    holonyms = list()
                    meronyms = list()
                    
                    synsetList = wordnet.synsets(word)
                    for synset in synsetList:
                        hypernyms.append(synset.hypernyms())
                        hyponyms.append(synset.hyponyms())
                        holonyms.append(synset.holonyms())
                        meronyms.append(synset.meronyms())
                        pass
                    
                    wordnetted = {"hypernyms" : hypernyms,
                     "hyponyms" : hyponyms,
                     "holonyms" : holonyms,
                     "meronyms" : meronyms}
                    pass
                pass
            pass
        
        container.append({"DOC {}".format(i) : {"word" : word, "pos" : pos, "stemmed" : stemmed, "lemma" : lemma, "deptree" : parse_tree, "wordneted" : wordnetted}})
        pass
    pass

In [165]:
createContainer()

In [166]:
def cosSim():
    for main in range(len(qaDocs)):
        similarity = list()
        tfidfffffff = list()
        for sub in qaDocs:
            # print("From {} to {} : {}".format(qaDocs[main].name, sub.name, distance(qaDocs[main].vector, sub.vector, method=COSINE)))
            similarity.append({sub.name, distance(qaDocs[main].vector, sub.vector, method=COSINE)})
            tfidfffffff.append(sub.vector)
            pass
        container[main].update({"similarity" : similarity, "tfidf" : tfidf(tfidfffffff)})
        pass
    pass

In [167]:
cosSim()

In [168]:
container

[{'DOC 0': {'deptree': [Sentence('What/WP/O/O/what ways/NNS/B-NP/O/way do/VBP/B-VP/O/do you/PRP/B-NP/O/you support/VB/B-VP/O/support payment/NN/B-NP/O/payment ?/./O/O/?'),
    Sentence('You/PRP/B-NP/O/you can/MD/B-VP/O/can pay/VB/I-VP/O/pay using/VBG/I-VP/O/used a/DT/B-NP/O/a credit/NN/I-NP/O/credit or/CC/O/O/or debit/NN/B-NP/O/debit card/NN/I-NP/O/card ././O/O/.'),
    Sentence('You/PRP/B-NP/O/you can/MD/B-VP/O/can also/RB/I-VP/O/also use/VB/I-VP/O/use your/PRP$/B-NP/O/your GameLink/NN/I-NP/O/gamelink points/NNS/I-NP/O/point to/TO/B-VP/O/to pay/VB/I-VP/O/pay for/IN/B-PP/B-PNP/for items/NNS/B-NP/I-PNP/item ././O/O/.')],
   'lemma': u'item',
   'pos': u'NNS',
   'stemmed': u'item',
   'word': u'items',
   'wordneted': {'holonyms': [],
    'hypernyms': [],
    'hyponyms': [],
    'meronyms': []}},
  'similarity': [{-2.220446049250313e-16, 'DOC 0'},
   {1.0, 'DOC 1'},
   {1.0, 'DOC 2'},
   {0.9410744349011211, 'DOC 3'},
   {0.9398070734571154, 'DOC 4'},
   {1.0, 'DOC 5'},
   {1.0, 'DOC 6'

In [9]:
bagofwords = [Counter(re.findall(r'\w+', txt)) for txt in documents]

In [10]:
# Calculating the match score for the input query against each of the FAQs

def match_qa_pair(input_bag):
    match_score = dict()
    for word in input_bag:
        for w in word:
            for i in range(len(bagofwords)):
                if( w in bagofwords[i].keys()):
                    match_score[i] = match_score.get(i, 0) + 1
                    pass
                else:
                    match_score[i] = 0
                    pass
                pass
            pass
        pass
    
    #print(match_score)
    maximum = max(match_score.items(), key=lambda k : k[1])
    #print(maximum[0])
    for key in match_score:
        if key == maximum[0]:
            print("The matching question is: " + qlines[key])
            print("The matching answer is: " + alines[key])
            pass
        pass
    pass


In [13]:
document = Document(sentence, stemmer = LEMMA)
pos = parse(sentence, lemmata = True)
parse_tree = parsetree(sentence, lemmata = True)

In [10]:
faqDoc = Document(" ".join(corpus))

In [100]:
len(set(faqDoc.vector))

248

In [14]:
# pprint(parse(sentence, relations=True, lemmata=True))
# pprint(parsetree(sentence, relations=True, lemmata=True))

          WORD   TAG    CHUNK   ROLE   ID     PNP    LEMMA      
                                                                
          This   DT     -       -      -      -      this       
            is   VBZ    VP      -      1      -      be         
             a   DT     NP      OBJ    1      -      a          
          test   NN     NP ^    OBJ    1      -      test       
      sentence   NN     NP ^    OBJ    1      -      sentence   
          that   WDT    -       -      -      -      that       
          will   MD     VP      -      -      -      will       
            be   VB     VP ^    -      -      -      be         
          used   VBN    VP ^    -      -      -      used       
            to   TO     VP ^    -      -      -      to         
         parse   VB     VP ^    -      -      -      parse      
          into   IN     PP      -      -      PNP    into       
             a   DT     NP      -      -      PNP    a          
         parse   JJ     N

In [16]:
for word in sentence.split():
    synsetList = wordnet.synsets(word)
    
    print(word)
    for synset in synsetList:
        print("Definition : {}".format(synset.gloss))
        print("Synonyms : {}".format(synset.synonyms))
        print("Hypernyms : {}".format(synset.hypernyms()))
        print("Hyponyms : {}".format(synset.hyponyms()))
        print("Holonyms : {}".format(synset.holonyms()))
        print("Meronyms : {}".format(synset.meronyms()))
        pass
    
    print("\n")
    pass

This


is


a
Definition : a metric unit of length equal to one ten billionth of a meter (or 0.0001 micron); used to specify wavelengths of electromagnetic radiation
Synonyms : [u'angstrom', u'angstrom unit', u'A']
Hypernyms : [Synset(u'metric linear unit')]
Hyponyms : []
Holonyms : [Synset(u'nanometer')]
Meronyms : [Synset(u'picometer')]
Definition : any of several fat-soluble vitamins essential for normal vision; prevents night blindness or inflammation or dryness of the eyes
Synonyms : [u'vitamin A', u'antiophthalmic factor', u'axerophthol', u'A']
Hypernyms : [Synset(u'fat-soluble vitamin')]
Hyponyms : [Synset(u'vitamin A1'), Synset(u'vitamin A2')]
Holonyms : []
Meronyms : []
Definition : one of the four nucleotides used in building DNA; all four nucleotides have a common phosphate group and a sugar (ribose)
Synonyms : [u'deoxyadenosine monophosphate', u'A']
Hypernyms : [Synset(u'nucleotide')]
Hyponyms : []
Holonyms : []
Meronyms : []
Definition : (biochemistry) purine base found in

In [18]:
lsa = Model([document, Document(s)])
lsa.reduce(2)

In [19]:
lsa.terms
lsa.train()

In [20]:
lsa.predict("A sentence this is")

In [103]:
m = Model([document, Document(s)])
m.reduce(2)

for d in m.documents:
    print("\n")
    print(d.name)
    for concept, w1 in m.lsa.vectors[d.id].items():
        for feature, w2 in m.lsa.concepts[concept].items():
            if w1 != 0 and w2 != 0:
                print((feature, w1 * w2))
                pass
            pass
        pass
    pass



None
(u'sentence', 0.353553390593274)
(u'test', 0.353553390593274)
(u'parse', 0.707106781186547)
(u'tree', 0.353553390593274)
(u'spy', 0.353553390593274)


None
(u'vent', 0.113960576459638)
(u'bearing', 0.113960576459638)
(u'attached', 0.113960576459638)
(u'39th', 0.113960576459638)
(u'weather', 0.113960576459638)
(u'ready', 0.113960576459638)
(u'gaseous', 0.113960576459638)
(u'hydrogen', 0.227921152919276)
(u'grounded', 0.113960576459638)
(u'space', 0.113960576459638)
(u'leak', 0.227921152919276)
(u'window', 0.113960576459638)
(u'station', 0.113960576459638)
(u'potentially', 0.113960576459638)
(u'closed', 0.113960576459638)
(u'shuttle', 0.227921152919276)
(u'supplies', 0.113960576459638)
(u'intelligent', 0.113960576459638)
(u'final', 0.113960576459638)
(u'discovery', 0.227921152919276)
(u'conclude', 0.113960576459638)
(u'flight', 0.341881729378914)
(u'monday', 0.341881729378914)
(u'ship\u02bcs', 0.113960576459638)
(u'initially', 0.113960576459638)
(u'friday', 0.227921152919276)
(u'd

In [99]:
svm = SVM()
svm.train(document)

In [100]:
print(svm.classes)
print(svm.classify(Document("A sentence this is")))

[None]
None


In [104]:
print(kfoldcv(SVM, faqDoc.vector, folds=10))

TypeError: train() takes at most 3 arguments (6 given)

In [91]:
document.wordcount

In [31]:
Document("Installing collected packages. Found existing installation").wordcount

In [102]:
Document("This is a test sentence that will be used to parse into a parse tree and various other things.", stemmer = LEMMA).vector

{u'parse': 0.4, u'sentence': 0.2, u'test': 0.2, u'tree': 0.2}

In [101]:
s = '''
     The shuttle Discovery, already delayed three times by technical problems 
     and bad weather, was grounded again Friday, this time by a potentially 
     dangerous gaseous hydrogen leak in a vent line attached to the shipʼs 
     external tank. The Discovery was initially scheduled to make its 39th 
     and final flight last Monday, bearing fresh supplies and an intelligent 
     robot for the International Space Station. But complications delayed the 
     flight from Monday to Friday,  when the hydrogen leak led NASA to conclude 
     that the shuttle would not be ready to launch before its flight window 
     closed this Monday.
'''
d = Document(s, threshold=1)
print(d.keywords(top=6))

[(0.16666666666666663, u'flight'), (0.16666666666666663, u'monday'), (0.11111111111111108, u'delayed'), (0.11111111111111108, u'discovery'), (0.11111111111111108, u'friday'), (0.11111111111111108, u'hydrogen')]


In [102]:
d.keywords()

[(0.16666666666666663, u'flight'),
 (0.16666666666666663, u'monday'),
 (0.11111111111111108, u'delayed'),
 (0.11111111111111108, u'discovery'),
 (0.11111111111111108, u'friday'),
 (0.11111111111111108, u'hydrogen'),
 (0.11111111111111108, u'leak'),
 (0.11111111111111108, u'shuttle')]

In [28]:
pprint(parse(s, lemmata = True))

          WORD   TAG    CHUNK   ROLE   ID     PNP    LEMMA         
                                                                   
           The   DT     NP      -      -      -      the           
       shuttle   NN     NP ^    -      -      -      shuttle       
     Discovery   NNP    NP ^    -      -      -      discovery     
             ,   ,      -       -      -      -      ,             
       already   RB     VP      -      -      -      already       
       delayed   VBN    VP ^    -      -      -      delay         
         three   CD     NP      -      -      -      three         
         times   NNS    NP ^    -      -      -      time          
            by   IN     PP      -      -      PNP    by            
     technical   JJ     NP      -      -      PNP    technical     
      problems   NNS    NP ^    -      -      PNP    problem       
           and   CC     -       -      -      -      and           
           bad   JJ     NP      -      -      - 

In [33]:
pprint(parsetree(s, tokenize = True, lemmata = True))

          WORD   TAG    CHUNK   ROLE   ID     PNP    LEMMA         
                                                                   
           The   DT     NP      -      -      -      the           
       shuttle   NN     NP ^    -      -      -      shuttle       
     Discovery   NNP    NP ^    -      -      -      discovery     
             ,   ,      -       -      -      -      ,             
       already   RB     VP      -      -      -      already       
       delayed   VBN    VP ^    -      -      -      delay         
         three   CD     NP      -      -      -      three         
         times   NNS    NP ^    -      -      -      time          
            by   IN     PP      -      -      PNP    by            
     technical   JJ     NP      -      -      PNP    technical     
      problems   NNS    NP ^    -      -      PNP    problem       
           and   CC     -       -      -      -      and           
           bad   JJ     NP      -      -      - 

In [20]:
import operator
sorted(faqDoc.vector.items(), key=operator.itemgetter(1))

[(u'rating', 0.0017605633802816902),
 (u'misusing', 0.0017605633802816902),
 (u'indeed', 0.0017605633802816902),
 (u'displayed', 0.0017605633802816902),
 (u'gb', 0.0017605633802816902),
 (u'world', 0.0017605633802816902),
 (u'tcg', 0.0017605633802816902),
 (u'disk', 0.0017605633802816902),
 (u'guides', 0.0017605633802816902),
 (u'developer', 0.0017605633802816902),
 (u'content', 0.0017605633802816902),
 (u'copy', 0.0017605633802816902),
 (u'console', 0.0017605633802816902),
 (u'violate', 0.0017605633802816902),
 (u'earned', 0.0017605633802816902),
 (u'personal', 0.0017605633802816902),
 (u'sharing', 0.0017605633802816902),
 (u'participants', 0.0017605633802816902),
 (u'desktop', 0.0017605633802816902),
 (u'languages', 0.0017605633802816902),
 (u'explicitly', 0.0017605633802816902),
 (u'permanently', 0.0017605633802816902),
 (u'categorized', 0.0017605633802816902),
 (u'extensive', 0.0017605633802816902),
 (u'mainstream', 0.0017605633802816902),
 (u'permission', 0.0017605633802816902),
 

In [21]:
faqDoc.tf("games")

0.10035211267605634

In [22]:
faqDoc.tfidf("games")

0.10035211267605634

In [145]:
documents

['What ways do you support payment?\nYou can pay using a credit or debit card. You can also use your GameLink points to pay for items.\n',
 'Can I pre-order games on the site?\nYes, you can definitely pre-order games on our site. Some games also offer pre-order bonuses and discounts.\n',
 "Can I get a refund for a game I didn't like or wasn't able to run on my system?\nYes, you can get a refund for a game if you apply for it within 15 days of purchase. Please refrain from misusing this feature.\n",
 'How do I access the games after purchasing?\nAfter purchasing a game on the site, you will need to download and install the GameLink client. The game can then be downloaded and installed from within the client.\n',
 'Do you offer indie games on your site?\nYes, we have an extensive library of Indie games and also run special events to support indie developers.\n',
 'Do you also offer DRM free games?\nYes, we do have DRM free games on offer.\n',
 'Do you have games categorised by genres?\nY

In [185]:
model = Model(documents=qaDocs, weight=TFIDF)

In [186]:
gridsearch(SVM, model, kernel=[RADIAL], gamma=[0.1,1,10])

[((1.0, 1.0, 1.0, 1.0, 0.0), {'gamma': 10, 'kernel': 2}),
 ((1.0, 1.0, 1.0, 1.0, 0.0), {'gamma': 1, 'kernel': 2}),
 ((1.0, 1.0, 1.0, 1.0, 0.0), {'gamma': 0.1, 'kernel': 2})]

In [187]:
print(kfoldcv(SVM, qaDocs, folds=10))

(1.0, 1.0, 1.0, 1.0, 0.0)


In [197]:
from pattern.vector import KMEANS, COSINE, RANDOM
model = Model(documents=qaDocs, weight=TFIDF)
model.cluster(method=KMEANS, k=10, iterations=10, distance=COSINE, seed=RANDOM, p=0.8)

[[Document(id='Qq4GJDN-2367', name='QA 51'),
  Document(id='Qq4GJDN-2345', name='QA 29'),
  Document(id='Qq4GJDN-2334', name='QA 18'),
  Document(id='Qq4GJDN-2364', name='QA 48'),
  Document(id='Qq4GJDN-2348', name='QA 32'),
  Document(id='Qq4GJDN-2339', name='QA 23')],
 [Document(id='Qq4GJDN-2346', name='QA 30'),
  Document(id='Qq4GJDN-2331', name='QA 15'),
  Document(id='Qq4GJDN-2363', name='QA 47'),
  Document(id='Qq4GJDN-2322', name='QA 6'),
  Document(id='Qq4GJDN-2317', name='QA 1'),
  Document(id='Qq4GJDN-2370', name='QA 54')],
 [Document(id='Qq4GJDN-2352', name='QA 36'),
  Document(id='Qq4GJDN-2324', name='QA 8'),
  Document(id='Qq4GJDN-2366', name='QA 50'),
  Document(id='Qq4GJDN-2368', name='QA 52'),
  Document(id='Qq4GJDN-2355', name='QA 39')],
 [Document(id='Qq4GJDN-2362', name='QA 46'),
  Document(id='Qq4GJDN-2361', name='QA 45'),
  Document(id='Qq4GJDN-2337', name='QA 21'),
  Document(id='Qq4GJDN-2323', name='QA 7'),
  Document(id='Qq4GJDN-2344', name='QA 28'),
  Document(

In [189]:
model.documents[0].name

'QA 0'

In [190]:
model.reduce(2)

for d in model.documents:
    print(d.name)
    for concept, w1 in model.lsa.vectors[d.id].items():
        for feature, w2 in model.lsa.concepts[concept].items():
            if w1 != 0 and w2 != 0:
                print((feature, w1 * w2))
                pass
            pass
        pass
    pass

QA 0
(u'tcg', 1.1990844021893728e-18)
(u'mod', 1.1990844021893728e-33)
(u'officially', 1.1990844021893728e-33)
(u'community', -1.1990844021893728e-33)
(u'translation', -1.1990844021893728e-33)
(u'refund', 1.2248168857406966e-05)
(u'rating', 2.9086855924051503e-06)
(u'concept', 2.5694645459421426e-06)
(u'modding', 2.9008514785613664e-06)
(u'indeed', 2.468435224065914e-05)
(u'supported', 8.058038660822456e-05)
(u'vary', 8.341699396773494e-06)
(u'ost', 1.77938569812528e-05)
(u'installed', 8.50361765474083e-06)
(u'gb', 2.008643769111549e-06)
(u'world', 4.303440249117002e-06)
(u'disk', 2.008643769111549e-06)
(u'developer', 1.9382092141482024e-05)
(u'removed', 7.745600592587127e-06)
(u'depend', 4.658626074097911e-06)
(u'violate', 1.1541808236747076e-06)
(u'earned', 0.0022646940716522235)
(u'personal', 2.9008514785613664e-06)
(u'sharing', 2.291154308003197e-05)
(u'desktop', 4.8733975694384325e-05)
(u'window', 2.008643769111549e-06)
(u'explicitly', 8.74318326576155e-06)
(u'permanently', 7.7456

(u'indeed', 8.387168064891556e-06)
(u'supported', 2.7379338887568452e-05)
(u'vary', 2.834315201202768e-06)
(u'ost', 6.04593823525936e-06)
(u'installed', 2.889331254656648e-06)
(u'gb', 6.824903772960393e-07)
(u'world', 1.4622087820927677e-06)
(u'disk', 6.824903772960393e-07)
(u'developer', 6.585583557346076e-06)
(u'removed', 2.6317747089407585e-06)
(u'depend', 1.5828926541805732e-06)
(u'violate', 3.9216376638353497e-07)
(u'earned', 0.0007694903074354912)
(u'personal', 9.856417800548152e-07)
(u'sharing', 7.784808795659122e-06)
(u'desktop', 1.655867006896297e-05)
(u'window', 6.824903772960393e-07)
(u'explicitly', 2.970730070497949e-06)
(u'permanently', 2.6317747089407585e-06)
(u'extensive', 1.3213119677677412e-06)
(u'include', 3.1136718139970896e-06)
(u'local', 3.68669575678732e-06)
(u'duo', 6.824903772960393e-07)
(u'crash', 8.256292439869904e-07)
(u'mainstream', 1.655867006896297e-05)
(u'permission', 5.422592164611093e-07)
(u'displayed', 3.253815093104951e-06)
(u'banned', 5.2635494178834

(u'term', 6.587884580786166e-07)
(u'game', 2.2775269677571715e-05)
(u'marked', 1.58166717106603e-05)
(u'background', 2.0391522386818836e-06)
(u'party', 2.211410058925414e-06)
(u'using', 3.367209709862768e-06)
(u'ticket', 0.000121830844986237)
(u'day', 6.547268507264185e-06)
(u'mod', 3.330715872300121e-05)
(u'register', 3.9001123213859915e-06)
(u'earn', 0.00024563351215091547)
(u'intel', 1.1465026140957326e-06)
(u'level', 4.785149432503179e-06)
(u'edit', 2.3925747162515895e-06)
(u'server', 3.664164296148649e-05)
(u'specific', 6.585931083004157e-06)
(u'item', 3.367209709862768e-06)
(u'categorised', 1.921950917295512e-06)
(u'common', 2.6043360125895273e-06)
(u'team', 5.742630425552079e-06)
(u'deleting', 3.3387240278583873e-06)
(u'page', 9.602070323086043e-05)
(u'requirement', 2.2930052281882774e-06)
(u'set', 5.828259853267636e-06)
(u'art', 1.4666103885867142e-06)
(u'play', 2.4804658671940688e-05)
(u'library', 3.4252268943961215e-06)
(u'streaming', 2.7875887344524454e-06)
(u'specified', 4.

(u'delete', 9.112124526091536e-06)
(u'backup', 1.797981029960948e-06)
(u'create', 3.785320944255224e-06)
(u'automatically', 1.3002155735636821e-05)
(u'rigorously', 1.5672922681937834e-05)
(u'pentium', 3.1290620314704546e-06)
(u'community', 4.4425041729722436e-05)
(u'synced', 1.14661112079953e-05)
(u'unexpected', 3.785320944255224e-06)
(u'apply', 9.540088868939993e-06)
(u'quality', 1.5672922681937834e-05)
(u'engineer', 1.5672922681937834e-05)
(u'save', 1.14661112079953e-05)
(u'fee', 1.0644278724950204e-05)
(u'raise', 0.0003325036215543817)
(u'service', 1.721289093602622e-05)
(u'misusing', 9.540088868939993e-06)
(u'support', 0.0003228413349566206)
(u'system', 0.0007020171521395117)
(u'approved', 4.531145735565547e-06)
(u'migrate', 0.0003325036215543817)
(u'editor', 1.3059742926070508e-05)
(u'lot', 1.499316747391657e-05)
(u'memory', 3.1290620314704546e-06)
(u'translate', 0.0007311066982894133)
(u'store', 0.0005346360279877693)
(u'buy', 0.0035279367807650635)
(u'invite', 7.107815397884998e

(u'tcg', 5.604647605392254e-17)
(u'mod', 5.604647605392255e-32)
(u'officially', 5.604647605392255e-32)
(u'community', -5.604647605392255e-32)
(u'translation', -5.604647605392255e-32)
(u'refund', 1.4380628612858696e-05)
(u'rating', 3.4151004728070692e-06)
(u'concept', 3.016819558848266e-06)
(u'modding', 3.405902405486975e-06)
(u'indeed', 2.8982005902640435e-05)
(u'supported', 9.460978426931781e-05)
(u'vary', 9.794025737370776e-06)
(u'ost', 2.0891845288610165e-05)
(u'installed', 9.984134672067668e-06)
(u'gb', 2.358357432479191e-06)
(u'world', 5.052688014074417e-06)
(u'disk', 2.358357432479191e-06)
(u'developer', 2.275659913508644e-05)
(u'removed', 9.094143524823607e-06)
(u'depend', 5.4697132443000255e-06)
(u'violate', 1.3551287519449836e-06)
(u'earned', 0.0026589872123193663)
(u'personal', 3.405902405486975e-06)
(u'sharing', 2.6900542915213075e-05)
(u'desktop', 5.721877396107304e-05)
(u'window', 2.358357432479191e-06)
(u'explicitly', 1.0265409703511911e-05)
(u'permanently', 9.09414352482

...

(u'indeed', 1.8202662497003735e-05)
(u'supported', 5.942135191587366e-05)
(u'vary', 6.151311457985943e-06)
(u'ost', 1.3121493729788451e-05)
(u'installed', 6.270712743996902e-06)
(u'gb', 1.4812081860354582e-06)
(u'world', 3.1734302633094632e-06)
(u'disk', 1.4812081860354582e-06)
(u'developer', 1.4292685434787198e-05)
(u'removed', 5.71173802937479e-06)
(u'depend', 3.435350350691699e-06)
(u'violate', 8.511126315585051e-07)
(u'earned', 0.001670024047758842)
(u'personal', 2.1391373734819477e-06)
(u'sharing', 1.68953627749823e-05)
(u'desktop', 3.593726515702862e-05)
(u'window', 1.4812081860354582e-06)
(u'explicitly', 6.447372512938127e-06)
(u'permanently', 5.71173802937479e-06)
(u'extensive', 2.86764204752335e-06)
(u'include', 6.7575988364739225e-06)
(u'local', 8.001232128737968e-06)
(u'duo', 1.4812081860354582e-06)
(u'crash', 1.7918623258380902e-06)
(u'mainstream', 3.593726515702862e-05)
(u'permission', 1.1768646373558619e-06)
(u'displayed', 7.061751655528798e-06)
(u'banned', 1.142347605875

(u'ye', 0.0005959540496149249)
(u'term', 2.59094245495644e-06)
(u'game', 8.95726274604233e-05)
(u'marked', 6.220522798893343e-05)
(u'background', 8.019761188180794e-06)
(u'party', 8.697232224890969e-06)
(u'using', 1.3242864966805312e-05)
(u'ticket', 0.000479147296415429)
(u'day', 2.5749686005345435e-05)
(u'mod', 0.0001309933872264324)
(u'register', 1.5338712250741653e-05)
(u'earn', 0.0009660495523069985)
(u'intel', 4.509068519874836e-06)
(u'level', 1.881946574192057e-05)
(u'edit', 9.409732870960285e-06)
(u'server', 0.00014410754651828148)
(u'specific', 2.590174165792141e-05)
(u'item', 1.3242864966805312e-05)
(u'categorised', 7.558821298246192e-06)
(u'common', 1.0242566728734247e-05)
(u'team', 2.258513304267981e-05)
(u'deleting', 1.313083391653647e-05)
(u'page', 0.00037763885129560147)
(u'requirement', 9.018137039737135e-06)
(u'set', 2.2921904151737986e-05)
(u'art', 5.768017144307676e-06)
(u'play', 9.755399088392223e-05)
(u'library', 1.347104016429271e-05)
(u'streaming', 1.0963279502673

(u'tcg', 2.7001199694409767e-16)
(u'mod', 2.700119969440977e-31)
(u'officially', 2.700119969440977e-31)
(u'community', -2.700119969440977e-31)
(u'translation', -2.700119969440977e-31)
(u'refund', 6.070943905670581e-05)
(u'rating', 1.441723026217513e-05)
(u'concept', 1.2735842645238094e-05)
(u'modding', 1.437839958776988e-05)
(u'indeed', 0.00012235079344961083)
(u'supported', 0.0003994058317541415)
(u'vary', 4.1346579807440145e-05)
(u'ost', 8.819727165451608e-05)
(u'installed', 4.214914603008748e-05)
(u'gb', 9.956070814109096e-06)
(u'world', 2.1330490016877038e-05)
(u'disk', 9.956070814109096e-06)
(u'developer', 9.606953948411445e-05)
(u'removed', 3.8391948429816493e-05)
(u'depend', 2.309100887047238e-05)
(u'violate', 5.7208282471484874e-06)
(u'earned', 0.011225213199270096)
(u'personal', 1.437839958776988e-05)
(u'sharing', 0.00011356366363867758)
(u'desktop', 0.00024155548162777118)
(u'window', 9.956070814109096e-06)
(u'explicitly', 4.33365801707876e-05)
(u'permanently', 3.839194842981

(u'account', 0.031245257070200854)
(u'graphic', 0.00030844264503897625)
(u'15', 0.0012053643859952221)
(u'unfortunately', 0.0035182430345303585)
(u'mb', 0.0006168852900770949)
(u'setup', 0.002389819109204854)
(u'getting', 0.0011893963334522755)
(u'ram', 0.00030844264503897625)
(u'minimum', 0.0006168852900770949)
(u'crossed', 0.0006617228402815731)
(u'friend', 0.0016388219451261956)
(u'install', 0.00021985437355312288)
(u'guide', 0.0008553026863614624)
(u'pack', 0.0020222498646144827)
(u'30', 0.0011893963334522755)
(u'constant', 0.0014705193907073979)
(u'purchased', 0.001348046652113104)
(u'stream', 0.00024506699667280126)
(u'played', 0.00034831637890179746)
(u'indie', 0.0017914492503516796)
(u'microtransaction', 0.0015650901557110143)
(u'partnership', 0.0004276513431803024)
(u'share', 0.003969063109672271)
(u'site', 0.001341586194215104)
(u'player', 0.001321652463834154)
(u'single', 0.010064319959301354)
(u'sometime', 0.0014270054537667322)
(u'manner', 0.0014270054537667322)
(u'categor

(u'permitted', 1.1947346049028062e-06)
(u'card', 4.4162754082056995e-06)
(u'official', 1.698089244893419e-06)
(u'publisher', 1.1209662138295953e-05)
(u'installation', 8.048848682681806e-06)
(u'language', 3.563952996872069e-05)
(u'downloaded', 3.063157682378244e-06)
(u'country', 1.0250342458453502e-05)
(u'region', 1.3710556321163662e-05)
(u'larger', 2.2475133675283784e-05)
(u'allows', 0.0002693215823389043)
(u'o', 3.64829504819993e-05)
(u'credit', 4.6404753480562165e-06)
(u'connection', 8.207492138023216e-06)
(u'drm', 8.960720997776018e-06)
(u'massive', 2.520741297154457e-06)
(u'delete', 4.378914914574003e-06)
(u'backup', 8.640362547365425e-07)
(u'create', 1.8190706560019238e-06)
(u'automatically', 6.24830504778179e-06)
(u'rigorously', 7.531766569957139e-06)
(u'pentium', 1.5036994236634252e-06)
(u'community', 2.1348860768290588e-05)
(u'synced', 5.51014477876006e-06)
(u'unexpected', 1.8190706560019238e-06)
(u'apply', 4.584577099988494e-06)
(u'quality', 7.531766569957139e-06)
(u'engineer'

In [191]:
qaDocs[0].words

{u'card': 1,
 u'credit': 1,
 u'debit': 1,
 u'gamelink': 1,
 u'item': 1,
 u'pay': 2,
 u'payment': 1,
 u'support': 1,
 u'using': 1}

In [192]:
from pattern.vector import LSA, L2
# lsa = LSA(model, k=L2)
model = Model(documents=qaDocs, weight=TFIDF)

In [193]:
lsa = LSA(model, k=L2)
lsa.concepts

[{u'1': -0.0,
  u'10': -0.0,
  u'15': -0.0,
  u'256': -0.0,
  u'3': -0.0,
  u'30': -0.0,
  u'300': -0.0,
  u'able': -0.0,
  u'acces': 0.0,
  u'account': -0.0,
  u'achievement': 0.0,
  u'adhere': -0.0,
  u'allow': -0.0,
  u'allowed': 0.0,
  u'allows': -0.0,
  u'apply': -0.0,
  u'approved': -0.0,
  u'art': 0.0,
  u'assurance': -0.0,
  u'automatically': -0.0,
  u'available': -0.0,
  u'background': -0.0,
  u'backup': -0.0,
  u'banned': -0.0,
  u'bonuse': 0.0,
  u'book': 0.0,
  u'buy': -0.0,
  u'card': 0.0,
  u'categorised': -0.0,
  u'categorized': -0.0,
  u'change': -0.0,
  u'changing': -0.0,
  u'chat': 0.0,
  u'client': -0.0,
  u'common': -0.0,
  u'community': -1e-15,
  u'concept': 0.0,
  u'conflict': -0.0,
  u'connected': -0.0,
  u'connecting': -0.0,
  u'connection': -0.0,
  u'considered': -0.0,
  u'console': -0.0,
  u'constant': -0.0,
  u'content': -0.0,
  u'copy': -0.0,
  u'core2': -0.0,
  u'country': -0.0,
  u'crash': -0.0,
  u'create': -0.0,
  u'credit': -0.0,
  u'crossed': -0.0,
  u

In [200]:
model.documents[0].words

{u'card': 1,
 u'credit': 1,
 u'debit': 1,
 u'gamelink': 1,
 u'item': 1,
 u'pay': 2,
 u'payment': 1,
 u'support': 1,
 u'using': 1}

In [206]:
from pattern.vector import CLASSIFICATION, LINEAR
svm = SVM(type = CLASSIFICATION, kernel = LINEAR, train = qaDocs)

In [234]:
svm.test([qaDocs[0]])

(1.0, 1.0, 1.0, 1.0)

In [12]:
# word, POS, stop, lemma, stem, deptree, wordnet (hyper, hypo, mero, holo)
documents

['What ways do you support payment?\nYou can pay using a credit or debit card. You can also use your GameLink points to pay for items.\n',
 'Can I pre-order games on the site?\nYes, you can definitely pre-order games on our site. Some games also offer pre-order bonuses and discounts.\n',
 "Can I get a refund for a game I didn't like or wasn't able to run on my system?\nYes, you can get a refund for a game if you apply for it within 15 days of purchase. Please refrain from misusing this feature.\n",
 'How do I access the games after purchasing?\nAfter purchasing a game on the site, you will need to download and install the GameLink client. The game can then be downloaded and installed from within the client.\n',
 'Do you offer indie games on your site?\nYes, we have an extensive library of Indie games and also run special events to support indie developers.\n',
 'Do you also offer DRM free games?\nYes, we do have DRM free games on offer.\n',
 'Do you have games categorised by genres?\nY